# Conjugate Linear Regression using Covariates

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import hvplot.pandas
import adaptive_nof1
import numpy
from adaptive_nof1.policies import ThompsonSampling
from adaptive_nof1.inference import *
from adaptive_nof1.series_of_simulations_runner import simulate_configurations
from adaptive_nof1.helpers import *
from adaptive_nof1.models import SelfExperimentationModel
import pandas
import matplotlib.pyplot as plt
import holoviews
import panel

WARNING (pytensor.tensor.blas): Using NumPy C-API based implementation for BLAS functions.


In [3]:
# Constants
conjugate_normal_model_priors = {
    "mean": 2.5,
    "l": 0.5,
    "alpha": 10,
    "beta": 10,
}
N_INTERVENTIONS = 2
N_PATIENTS = 10
LENGTH = 200

In [4]:
# Generate random data with a, b coefficients:
rng = numpy.random.default_rng()
x_0 = rng.normal(0, 0.1, size=12)
x_1 = rng.normal(0, 1, size=12)
x_2 = rng.normal(0, 1, size=12)
x = numpy.stack((x_0, x_1), axis=-1)
y = x_0 + -2 * x_1

In [5]:
data_generating_model_1_1 = lambda patient_id: SelfExperimentationModel(
    patient_id,
    intervention_effects=[0, 0],
    baseline_model="noise",
    baseline_config={"variance": 1},
)
data_generating_model_1_2 = lambda patient_id: SelfExperimentationModel(
    patient_id,
    intervention_effects=[0, -1],
    baseline_model="noise",
    baseline_config={"variance": 1},
)
data_generating_model_1_3 = lambda patient_id: SelfExperimentationModel(
    patient_id,
    intervention_effects=[0, 1],
    baseline_model="noise",
    baseline_config={"variance": 1},
)
ts_one = ThompsonSampling(
    inference_model=ConjugateNormalModel(**conjugate_normal_model_priors),
    number_of_actions=N_INTERVENTIONS,
)
ts_two = ThompsonSampling(
    inference_model=BayesianLinearRegressionModel(
        mean=numpy.array(
            [
                conjugate_normal_model_priors["mean"],
                conjugate_normal_model_priors["mean"],
            ]
        ),
        # mean=numpy.array([-10, 10]),
        v=numpy.eye(N_INTERVENTIONS) * conjugate_normal_model_priors["l"],
        alpha=conjugate_normal_model_priors["alpha"],
        beta=conjugate_normal_model_priors["beta"],
    ),
    number_of_actions=N_INTERVENTIONS,
)

In [6]:
# Full crossover study
study_designs = {
    "n_patients": [N_PATIENTS],
    "policy": [ts_two, ts_one],
    # "policy": [ts_two],
    "model_from_patient_id": [
        data_generating_model_1_1,
        data_generating_model_1_2,
        data_generating_model_1_3,
    ],
}
configurations = generate_configuration_cross_product(study_designs)

In [7]:
calculated_series, config_to_simulation_data = simulate_configurations(
    configurations, LENGTH
)

  0%|          | 0/200 [00:00<?, ?it/s]

  0%|          | 0/200 [00:00<?, ?it/s]

  0%|          | 0/200 [00:00<?, ?it/s]

  0%|          | 0/200 [00:00<?, ?it/s]

  0%|          | 0/200 [00:00<?, ?it/s]

  0%|          | 0/200 [00:00<?, ?it/s]

In [8]:
def plot_allocations_for_calculated_series(calculated_series):
    panels = [series["result"].plot_allocations() for series in calculated_series]
    for panel, i in zip(panels, range(len(panels))):
        panel.opts(
            title=f"{calculated_series[i]['configuration']['policy']}, {calculated_series[i]['configuration']['model']}",
            fontsize={"title": "80%"},
        )
    return holoviews.Layout(panels).cols(1)


plot_allocations_for_calculated_series(calculated_series)

/opt/homebrew/Caskroom/miniconda/base/envs/mt/lib/python3.11/site-packages/holoviews/plotting/bokeh/plot.py:987: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  layout_plot = gridplot(
/opt/homebrew/Caskroom/miniconda/base/envs/mt/lib/python3.11/site-packages/holoviews/plotting/bokeh/plot.py:987: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  layout_plot = gridplot(


:Layout
   .HeatMap.I   :HeatMap   [t,patient_id]   (treatment,debug_info,context,outcome,counterfactual_outcomes,debug_data,treatment)
   .HeatMap.II  :HeatMap   [t,patient_id]   (treatment,debug_info,context,outcome,counterfactual_outcomes,debug_data,treatment)
   .HeatMap.III :HeatMap   [t,patient_id]   (treatment,debug_info,context,outcome,counterfactual_outcomes,debug_data,treatment)
   .HeatMap.IV  :HeatMap   [t,patient_id]   (treatment,debug_info,context,outcome,counterfactual_outcomes,debug_data,treatment)
   .HeatMap.V   :HeatMap   [t,patient_id]   (treatment,debug_info,context,outcome,counterfactual_outcomes,debug_data,treatment)
   .HeatMap.VI  :HeatMap   [t,patient_id]   (treatment,debug_info,context,outcome,counterfactual_outcomes,debug_data,treatment)

In [9]:
from adaptive_nof1.metrics import SimpleRegret
from adaptive_nof1 import SeriesOfSimulationsData

SeriesOfSimulationsData.plot_lines(
    [series["result"] for series in calculated_series],
    [
        SimpleRegret(),
    ],
    legend_position=(0, 1.5),
)

AssertionError: Simple Regret can only be calculated if the expectations of interventions are known

In [11]:
debug_data = calculated_series[0]["result"].simulations[0].history.debug_data()
debug_data[0]

{'probabilities': [0.5, 0.5],
 'mean': array([2.5, 2.5]),
 'v': array([[0.5, 0. ],
        [0. , 0.5]]),
 'alpha': 10,
 'beta': 10}

In [11]:
import param
from functools import reduce


class PatientExplorer(param.Parameterized):
    patient_id = param.Integer(default=0, bounds=(0, N_PATIENTS - 1))
    configuration = param.Integer(default=0, bounds=(0, len(calculated_series) - 1))
    t = param.Integer(default=10, bounds=(0, LENGTH - 1))

    @param.depends("patient_id", "configuration")
    def hvplot(self):
        debug_data = (
            calculated_series[self.configuration]["result"]
            .simulations[self.patient_id]
            .history.debug_data()
        )
        df = pandas.DataFrame([flatten_dictionary(d) for d in debug_data])
        return df.hvplot()

    @param.depends("configuration")
    def configuration_name(self):
        return panel.panel(calculated_series[self.configuration]["configuration"])

    @param.depends("patient_id", "configuration", "t")
    def posterior(self):
        debug_data = (
            calculated_series[self.configuration]["result"]
            .simulations[self.patient_id]
            .history.debug_data()
        )
        posterior_parameters = debug_data[self.t].copy()
        del posterior_parameters["probabilities"]

        if (
            calculated_series[self.configuration]["configuration"]["policy"]
            == "ThompsonSampling(BayesianLinearRegression)"
        ):
            model = BayesianLinearRegressionModel(
                **posterior_parameters,
            )
        elif (
            calculated_series[self.configuration]["configuration"]["policy"]
            == "ThompsonSampling(ConjugateNormalModel)"
        ):
            model = ConjugateNormalModel(
                **posterior_parameters,
            )
        curves = []
        for intervention in range(N_INTERVENTIONS):
            rv = model.posterior(intervention)
            x = np.linspace(rv.ppf(0.01), rv.ppf(0.99), 100)
            curves += [zip(x, rv.pdf(x))]
        return reduce(
            lambda x, y: x * y, [holoviews.Curve(curve) for curve in curves]
        ).opts(xlim=(-1, 7), ylim=(-0.01, 0.4))

In [12]:
explorer = PatientExplorer()
hvplot = holoviews.DynamicMap(explorer.hvplot)
panel.Column(
    panel.Row(panel.Column(explorer.param, explorer.configuration_name), hvplot),
    explorer.posterior,
)

Column
    [0] Row
        [0] Column
            [0] Column(margin=(5, 10), name='PatientExplorer')
                [0] StaticText(value='<b>PatientExplorer</b>')
                [1] IntSlider(end=9, name='Patient id')
                [2] IntSlider(end=5, name='Configuration')
                [3] IntSlider(end=199, name='T', value=10)
            [1] ParamMethod(method, _pane=JSON, defer_load=False)
        [1] HoloViews(DynamicMap, height=300, sizing_mode='fixed', width=700)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)